In [8]:
using Plots, Distances, Knet
plotly()

Plots.PlotlyBackend()

In [9]:
using Knet

function sigmoid(z) 
    return 1.0/(1.0+exp(-z)) 
end

function relu(z)
    return max(z,0)
end

function predict(w,x)
    n = length(w)
    for i = 1:2:n-3
        x = tanh.(w[i]*mat(x) .+ w[i+1])
    end
    x = w[end-1]*mat(x) .+ w[end]
    return x
end

function loss1(w,x,y)
    (d,n) = size(y)
    ypred = predict(w,x)
    l = sum(sum((y-ypred).^2,1).^(0.5))/n
    return l
end

function totalVar(y,ypred)
    max1 = maximum(y[1,:])
    min1 = minimum(y[1,:])
    max2 = maximum(y[2,:])
    min2 = minimum(y[2,:])
    
    d,m = size(y)
    n = m
    s1 = (max1-min1)/(n-1)
    s2 = (max2-min2)/(n-1)
    
    l=0
    
    Y = zeros(n,n)
    X = zeros(n,n)
    for k = 1:m
        i = Int(floor((y[1,k]-min1)/s1))+1
        j = Int(floor((y[2,k]-min2)/s2))+1
        Y[i,j] += 1
        
        r = Int(floor((ypred[1,k]-min1)/s1))+1
        s = Int(floor((ypred[2,k]-min2)/s2))+1
        if r > n || r < 1 || s > n || s < 1
            l += 10*vecnorm(y[:,k]-ypred[:,k],2)
        else
            X[r,s] += 1
        end
    end
    l += vecnorm(Y-X,2)/(n)
    
    return l
end

function loss2(w,x,y)
    ypred = predict(w,x)
    l = totalVar(y,ypred)
    l += totalVar(ypred,y)  
    return l
end

lossgradient = grad(loss2)

function train(w,xtrn, ytrn, mu=1e-2, epochs=10)
    p = optimizers(w,Adam; lr = mu)
    
    for epoch=1:epochs
        dtrn = minibatch(xtrn,ytrn,100;shuffle=true)
        for (x,y) in dtrn
            g = lossgradient(w, x, y)
            Knet.update!(w,g,p)
        end
        if epoch%100 == 0
            mu = mu/2
            report(epoch,w)
        end
    end
    report(epochs,w)
    return w
end

function init_weight(hidden_size)
    w = Any[]
    for h in hidden_size
        push!(w, randn(h[2],h[1]))
        push!(w, randn(h[2],1))
    end
    
    return w
end

report(epoch,w)=println((:epoch,epoch,:trn,loss2(w,xtrn,ytrn)))

report (generic function with 1 method)

In [10]:
using ProgressMeter

M = 10000
N = Int(M/50)
xtrn = randn(2,M)

2×10000 Array{Float64,2}:
 -1.21082  1.39498   -0.419546  0.131045  …  -1.0457     0.81846   -1.20172  
  1.3794   0.476893  -0.951467  1.02119      -0.903259  -0.221278  -0.0214186

In [109]:
dx = zeros(M)
@showprogress for i = 1:M
    for j = 1:M
        if sum(x[:,i] .> x[:,j]) == 2
            dx[i] += 1/M
        end
    end
end
px = sortperm(dx)
dx = dx[px]
x = x[:,px]
xtrn = zeros(2,M)

min1 = dx[1]
max1 = dx[end]

d = (max1-min1)/N

s_idx = 1
e_idx = 1
for i = 1:N-1
    s = min1 + (i-1)*d
    e = min1 + i*d
    x1 = Any[]
    while(dx[e_idx] < e && e_idx <= M)
        push!(x1,x[1,e_idx])
        e_idx += 1
    end
    p = sortperm(x1)
    for i = 0:length(p)-1
        xtrn[:,s_idx+i] = x[:,s_idx+p[i+1]-1]
    end
    
    s_idx = e_idx
    e_idx = s_idx
end

Progress: 100%|█████████████████████████████████████████| Time: 0:00:10


In [11]:
scatter(xtrn[1,:], xtrn[2,:])

In [12]:
A = randn(2,2)
B = rand(2,1)

ytrn = exp.(sin.(A*tanh.(rand(2,M))) .+ B)
ymean = sum(ytrn,2)/M
ytrn = ytrn .- sum(ytrn,2)/M

2×10000 Array{Float64,2}:
  0.385337   0.750749  -0.621672   …  -0.196651   -0.753247   -0.630367 
 -0.1311    -0.194338   0.0501258     -0.0142181   0.0124284  -0.0431146

In [13]:
ymean

2×1 Array{Float64,2}:
 1.80756 
 0.563735

In [131]:
dy = zeros(M)
@showprogress for i = 1:M
    for j = 1:M
        if sum(y[:,i] .> y[:,j]) == 2
           dy[i] += 1/M
        end
    end
end
py = sortperm(dy)
dy = dy[py]
y = y[:,py] 

ytrn = zeros(2,M)

min2 = dy[1]
max2 = dy[end]

d = (max2-min2)/N

s_idy = 1
e_idy = 1
for i = 1:N-1
    s = min2 + (i-1)*d
    e = min2 + i*d
    y1 = Any[]
    while(dy[e_idy] < e && e_idy <= M)
        push!(y1,y[1,e_idy])
        e_idy += 1
    end
    p = sortperm(y1)
    for i = 0:length(p)-1
        ytrn[:,s_idy+i] = y[:,s_idy+p[i+1]-1]
    end
    
    s_idy = e_idy
    e_idy = s_idy
end

Progress: 100%|█████████████████████████████████████████| Time: 0:00:09


In [14]:
scatter(ytrn[1,:], ytrn[2,:])

In [15]:
dtrn = minibatch(xtrn,ytrn,100;shuffle=true)

Knet.MB([-1.21082 1.39498 … 0.81846 -1.20172; 1.3794 0.476893 … -0.221278 -0.0214186], [0.385337 0.750749 … -0.753247 -0.630367; -0.1311 -0.194338 … 0.0124284 -0.0431146], 100, 10000, false, [3029, 3392, 6395, 4502, 1998, 8061, 1845, 1799, 6913, 9626  …  172, 9741, 164, 7088, 6301, 439, 592, 4286, 7373, 5345], [2, 10000], [2, 10000], Array{Float64,2}, Array{Float64,2})

In [ ]:
w = init_weight([(2,128),(128,128),(128,128),(128,128),(128,128),(128,128),(128,2)])

In [30]:
w = train(w,xtrn,ytrn,1e-7,200)

(:epoch, 100, :trn, 897.5630529771499)
(:epoch, 200, :trn, 892.1564086005318)
(:epoch, 200, :trn, 892.1564086005318)


14-element Array{Any,1}:
 [-1.66389 1.02194; -0.846482 -1.48929; … ; 0.494499 1.02895; -1.49999 0.978769]                                                                                      
 [1.07208; 2.47368; … ; -0.766057; 0.510957]                                                                                                                          
 [-0.943417 -0.244658 … 0.62065 -0.761248; 0.669245 0.838356 … 0.894106 -0.088518; … ; -2.33897 0.227834 … -0.810056 -1.19907; 0.103465 -1.17173 … -0.964559 0.616575]
 [-0.161318; 0.0310855; … ; 0.521212; -1.57415]                                                                                                                       
 [0.910229 -0.0913635 … 0.671619 -0.100022; 1.82372 -0.0466935 … 0.640985 0.108912; … ; -1.5609 -0.86649 … -0.902009 -1.16057; -0.227495 1.21895 … 0.293061 -1.34228] 
 [-0.944546; -0.903903; … ; 1.19425; -0.511134]                                                                                             

In [29]:
ypred = predict(w,xtrn)
scatter(ypred[1,:],ypred[2,:])

In [ ]:
sum(xtrn[:,1] .> xtrn[:,2])

$$f(x) = \sum_{n=0}^\infty f^{(n)}(0) \frac{x^n}{n!} $$